In [1]:
print('loading transcription model')
from interactive.offline_lyrics import setup_model
from transformers import pipeline

from interactive.voice_transcription import transcribe_audio

print('loading voice model')
from interactive.voice_gen import *
from interactive.utils import *
from scipy.io.wavfile import read, write
import os
import subprocess

model, tokenizer = setup_model()
pipe = pipeline(
    "text-generation",
    model=model,
    tokenizer=tokenizer,
)

generation_args = {
    "max_new_tokens": 500,
    "return_full_text": False,
    "temperature": 0.0,
    "do_sample": False,
}

def generate_clean(from_human):
    message = [{"role": "user", "content": from_human}]
    output = pipe(message, **generation_args)
    robot_response = output[0]['generated_text']
    robot_response = robot_response.replace(',\n',' ')
    robot_response = robot_response.replace('\n',' ')
    print('Robot: ', robot_response)
    return robot_response
    

loading transcription model
loading voice model


Lightning automatically upgraded your loaded checkpoint from v1.8.6 to v2.0.7. To apply the upgrade to your files permanently, run `python -m pytorch_lightning.utilities.upgrade_checkpoint --file hifigan_ft/HifiGan/2023-02-25_14-16-34/checkpoints/HifiGan--val_loss=0.4404-epoch=196-last.ckpt`
[NeMo W 2024-05-03 12:18:18 modelPT:165] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    dataset:
      _target_: nemo.collections.tts.torch.data.VocoderDataset
      manifest_filepath: hifigan_train_ft.json
      sample_rate: 22050
      n_segments: 8192
      max_duration: null
      min_duration: 0.75
      load_precomputed_mel: true
      hop_length: 256
    dataloader_params:
      drop_last: false
      shuffle: true
      batch_size: 4
      num_workers: 4
      pin_memory: true
    
[NeMo W 2024-05-03 12:18:18 modelPT:172] If you intend to do valid

[NeMo I 2024-05-03 12:18:18 features:289] PADDING: 0
[NeMo I 2024-05-03 12:18:18 features:297] STFT using exact pad
[NeMo I 2024-05-03 12:18:18 features:289] PADDING: 0
[NeMo I 2024-05-03 12:18:18 features:297] STFT using exact pad


Lightning automatically upgraded your loaded checkpoint from v1.8.6 to v2.0.7. To apply the upgrade to your files permanently, run `python -m pytorch_lightning.utilities.upgrade_checkpoint --file icecub/FastPitch/2023-02-25_10-50-19/checkpoints/FastPitch--val_loss=0.7854-epoch=782-last.ckpt`
 NeMo-text-processing :: INFO     :: Creating ClassifyFst grammars.
[NeMo W 2024-05-03 12:18:32 deprecated:65] Function ``g2p_backward_compatible_support`` is deprecated. But it will not be removed until a further notice. G2P object root directory `nemo_text_processing.g2p` has been replaced with `nemo.collections.tts.g2p`. Please use the latter instead as of NeMo 1.18.0.
[NeMo W 2024-05-03 12:18:33 en_us_arpabet:66] apply_to_oov_word=None, This means that some of words will remain unchanged if they are not handled by any of the rules in self.parse_one_word(). This may be intended if phonemes and chars are both valid inputs, otherwise, you may see unexpected deletions in your input.
[NeMo W 2024-05

[NeMo I 2024-05-03 12:18:33 features:289] PADDING: 1


`flash-attention` package not found, consider installing for better performance: No module named 'flash_attn'.
Current `flash-attenton` does not support `window_size`. Either upgrade or use `attn_implementation='eager'`.


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
Process ForkProcess-12:
Process ForkProcess-10:
Process ForkProcess-9:
Process ForkProcess-8:
Process ForkProcess-6:
Process ForkProcess-4:
Process ForkProcess-7:
Process ForkProcess-19:
Process ForkProcess-20:
Process ForkProcess-1:
Process ForkProcess-5:
Process ForkProcess-17:
Process ForkProcess-11:
Process ForkProcess-3:
Process ForkProcess-18:
Process ForkProcess-2:
Traceback (most recent call last):
Process ForkProcess-13:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/richard/anacon

In [15]:
folder_path = 'audio'
audio_length = 0
checked_files = set()
while True:
    for filename in os.listdir(folder_path):
        if filename.endswith('.wav') and filename not in checked_files:
            file_path = os.path.join(folder_path, filename)
            print(f"Checking file: {file_path}")
            is_file_complete(file_path)
            if check_wav_duration(file_path):
                print(f"File {filename} is complete and correct duration. Changing Name")
                target_fp = 'voice.wav'
                shutil.move(file_path, target_fp)
                input_text = transcribe_audio()
                print('Human: ', input_text)    

                # PARAPHRASE, WRITE AUDIO
                from_human = "Can you repeat this in rhyme, but keep it short : you asked" + input_text
                
                robot_response = generate_clean(from_human)
                spec, audio = infer(spec_model, vocoder, 
                                    robot_response, 
                                    speaker=None)
                write('gen/para.wav', 22050, audio[0])

                audio_length = len(audio[0])/22050
                # SEND
                command = [
                    "scp",
                    "-i", "/home/richard/.ssh/id_rsa",
                    "-o", "StrictHostKeyChecking=no",
                    "gen/para.wav",
                    "keirzomac@192.168.50.189:~/Desktop/zokeir/recordings/to_play/para.wav"]
                    
                subprocess.run(command)

                
                # ANSWER
                from_human = "Can you answer in rhyme, but keep it short :" + input_text
                robot_response = generate_clean(from_human)
                spec, audio = infer(spec_model, vocoder, 
                                    robot_response, 
                                    speaker=None)
                write('gen/response.wav', 22050, audio[0])

                command = [
                    "scp",
                    "-i", "/home/richard/.ssh/id_rsa",
                    "-o", "StrictHostKeyChecking=no",
                    "gen/response.wav",
                    "keirzomac@192.168.50.189:~/Desktop/zokeir/recordings/to_play/response.wav"]
                    
                subprocess.run(command)
                audio_length += len(audio[0])/22050
                

                time.sleep(int(audio_length))
                print("Waiting " + str(int(audio_length)))



            else:
                print(f"File {filename} is not the correct duration.")
            checked_files.add(filename)
            
    print("Waiting ` seconds before next check...")
    time.sleep(1)  # Wait 10 seconds before checking for new files


    # write('chunks/chunk_0.wav', 22050, audio[0])
    # # then need to send back to macbook
    # !scp -i /home/richard/.ssh/id_rsa_mac -oStrictHostKeyChecking=no chunks/chunk_0.wav richardsavery@10.125.44.240:~/Desktop/chunks
    # !scp -i /home/richard/.ssh/id_rsa_mac -oStrictHostKeyChecking=no chunks/tiny.wav richardsavery@10.125.44.240:~/Desktop/chunks
    
    # # then save
    # save_wavs('voice.wav', 'chunks/chunk_0.wav')
    
    # # then delete files 
    # !rm chunks/chunk_0.wav
    # !rm voice.wav
    # !rm tiny.txt
    
    # time.sleep(8)

Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Checking file: audio/e25fdfe9-c22a-4c7f-b17e-e4ea9cbe322d.wav
File e25fdfe9-c22a-4c7f-b17e-e4ea9cbe322d.wav is complete and correct duration. Changing Name
Human:  What's one plus one?
Robot:   In a couple of lines, here's the fun  One plus one is two, that's what's done.
Robot:   In a world where numbers align  One plus one is two, quite divine.
Waiting 8
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds before next check...
Waiting ` seconds

KeyboardInterrupt: 

In [11]:
command = [
    "scp",
    "-i", "/home/richard/.ssh/id_rsa",
    "-o", "StrictHostKeyChecking=no",
    "audio/para.wav",
    "keirzomac@192.168.50.189:~/Desktop/drumming-robot/rap_audio/para.wav"]
    


import subprocess
subprocess.run(command)

CompletedProcess(args=['scp', '-i', '/home/richard/.ssh/id_rsa', '-o', 'StrictHostKeyChecking=no', 'audio/para.wav', 'keirzomac@192.168.50.189:~/Desktop/drumming-robot/rap_audio/para.wav'], returncode=0)

In [23]:
import IPython.display as ipd

ipd.display(ipd.Audio(audio, rate=22050))


In [18]:
def generate_clean(from_human):
    message = [{"role": "user", "content": from_human}]
    output = pipe(message, **generation_args)
    robot_response = output[0]['generated_text']
    robot_response = robot_response.replace(',\n',' ')
    robot_response = robot_response.replace('\n',' ')
    print('Robot: ', robot_response)
    return robot_response
    

In [2]:
messages = [
    {"role": "user", "content": "Can you provide ways to eat combinations of bananas and dragonfruits?"},
    {"role": "assistant", "content": "Sure! Here are some ways to eat bananas and dragonfruits together: 1. Banana and dragonfruit smoothie: Blend bananas and dragonfruits together with some milk and honey. 2. Banana and dragonfruit salad: Mix sliced bananas and dragonfruits together with some lemon juice and honey."},
    {"role": "user", "content": "What about solving an 2x + 3 = 7 equation?"},
]
output = pipe(messages, **generation_args)

output[0]['generated_text']




You are not running the flash-attention implementation, expect numerical differences.


'To solve the equation 2x + 3 = 7, you need to isolate the variable x. Here are the steps:\n\n1. Subtract 3 from both sides of the equation to get: 2x = 7 - 3, which simplifies to 2x = 4.\n\n2. Divide both sides of the equation by 2 to solve for x: x = 4 / 2.\n\n3. Simplify the right side of the equation to find the value of x: x = 2.\n\nSo, the solution to the equation 2x + 3 = 7 is x = 2.'

In [ ]:
import os
import time

run = True

while run:
    print('ready and listening')
    file = False
    while file == False:
        file = os.path.exists('tiny.txt')
        time.sleep(0.1)
    print('got that file')

    
    # READ THE TINY TXT HERE, and DECIDE WHAT TO DO
    # Standard listen to voice
    # call other type of text response. 
    # just say set text
    
    
    
    input_text = transcribe_audio()
    print('Human: ', input_text)

    robot_response = generate_lyrics(input_text)
    robot_response = robot_response.replace(',\n',', ')
    robot_response = robot_response.replace('\n',', ')
    print('Robot: ', robot_response)
 
    spec, audio = infer(spec_model, vocoder, 
                        robot_response, 
                        speaker=None)
#     ipd.display(ipd.Audio(audio, rate=22050))
    write('chunks/chunk_0.wav', 22050, audio[0])
    # then need to send back to macbook
    !scp -i /home/richard/.ssh/id_rsa_mac -oStrictHostKeyChecking=no chunks/chunk_0.wav richardsavery@10.125.44.240:~/Desktop/chunks
    !scp -i /home/richard/.ssh/id_rsa_mac -oStrictHostKeyChecking=no chunks/tiny.wav richardsavery@10.125.44.240:~/Desktop/chunks
    
    # then save
    save_wavs('voice.wav', 'chunks/chunk_0.wav')
    
    # then delete files 
    !rm chunks/chunk_0.wav
    !rm voice.wav
    !rm tiny.txt
    
    time.sleep(8)
    # then delete files 

ready and listening
got that file
Human:  こんにちは
Robot:  Yo, what's up? Feeling fine?, I'm Keirzo, here to rhyme., Let's chat and have some fun, With my beats, we'll be number one.
chunk_0.wav                                   100%  572KB   6.1MB/s   00:00    
tiny.wav                                      100%    0     0.0KB/s   00:00    
ready and listening
got that file
Human:  大阪人にお招きします!
Robot:  Osaka, Osaka, what a great city, I'll bring the beats, make it sound so pretty, As a robot drummer named Keirzo, I'll join the party and put on a show!, , Let's jam together in Osaka town, Rocking to the rhythm, shaking the ground!
chunk_0.wav                                   100% 1151KB   9.0MB/s   00:00    
tiny.wav                                      100%    0     0.0KB/s   00:00    
ready and listening


# 

In [40]:
robot_response = generate_lyrics('introduce yourself as a drum teacher')
robot_response = robot_response.replace(',\n',', ')
robot_response = robot_response.replace('\n',', ')

In [9]:
# robot_response = "This cool beat I've got, it's our rhythmic state. Now, who's up for a try? Don't you hesitate."
# robot_response = "Now smell close, and watch me move. Can you hear the pulse? Can you feel the groove?"
robot_response = "Grab these dimport IPython.display as ipdrumsticks, participate. Let’s get into our rhythmic state"
# robot_response = "Great job superstar, your skills have come alive. Now that you’ve come this far, I hope you keep the drive"
# robot_response = "That’s okay, drumming takes time. Tap along with me, Feel the rhythm, let’s repeat."
# robot_response = "With practice, you'll reach your prime. So let’s jump back on this beat"
# robot_response = "Re member kids, it's all about the groove, with practice and patience, you'll im prove."

In [3]:
import IPython.display as ipd

spec, audio = infer(spec_model, vocoder, 
                    output[0]['generated_text'], 
                    speaker=None)

ipd.display(ipd.Audio(audio, rate=22050))

 NeMo-text-processing :: INFO     :: Skipping post-processing of To solve the equation two x + three = seven, you need to isolate the variable x. Here are the steps: one. Subtract three from both sides of the equation to get: two x = seven - three, which simplifies to two x = four.two. Divide both sides of the equation by two to solve for x: x equals four divided two.three. Simplify the right side of the equation to find the value of x: x = two.So, the solution to the equation two x + three = seven is x = two. for '/'
 NeMo-text-processing :: INFO     :: Skipping post-processing of To solve the equation two x + three = seven, you need to isolate the variable x. Here are the steps:one. Subtract three from both sides of the equation to get: two x = seven - three, which simplifies to two x = four.two. Divide both sides of the equation by two to solve for x: x equals four divided two.three. Simplify the right side of the equation to find the value of x: x = two.So, the solution to the equa

In [104]:
write('chunks/1_Introduction 2.wav', 22050, audio[0])

In [1]:
# FOR SENDING EXTRA COMMANDS TO KEIRZO
file_path = 'test.txt'
with open(file_path, 'r') as file:
    # Read the first line
    interaction_type = file.readline()
#     file.readline()
# Extract and print the string from the first line
interaction_type_str = interaction_type.strip()

In [7]:
import time
print (time.time())

1694057611.3774252


In [5]:
# import datetime
# import shutil

# original_human_path = "path_to_human_file.txt"
# original_robot_path = "path_to_robot_file.txt"

# def save_wavs(human_fp, robot_fp)
#     current_datetime = datetime.datetime.now()
#     formatted_datetime = current_datetime.strftime("%Y-%m-%d_%H-%M-%S")

#     new_human_filename = f"saved_interactions/{formatted_datetime}_human.wav"
#     new_robot_filename = f"saved_interactions/{formatted_datetime}_robot.wav"
    

# # shutil.copyfile(original_human_path, new_human_path)
# # shutil.copyfile(original_robot_path, new_robot_path)

In [6]:
new_human_filename

'saved_interactions/2023-08-29_13-42-16_human.wav'

/home/richard/rapping-robot/voice.wav

In [11]:
# this is it
!scp -i /home/richard/.ssh/id_rsa_mac -r chunks/ richardsavery@10.17.18.232:~/Desktop

chunk_7.wav                                   100%   67KB   1.1MB/s   00:00    
chunk_3.wav                                   100%   36KB   1.4MB/s   00:00    
chunk_2.wav                                   100%   21KB 889.0KB/s   00:00    
chunk_10.wav                                  100%   59KB   1.3MB/s   00:00    
chunk_4.wav                                   100%  118KB   1.8MB/s   00:00    
chunk_8.wav                                   100%   38KB   1.4MB/s   00:00    
chunk_6.wav                                   100%   75KB   1.7MB/s   00:00    
chunk_11.wav                                  100%  111KB   2.1MB/s   00:00    
chunk_5.wav                                   100%   24KB   1.3MB/s   00:00    
chunk_12.wav                                  100%   50KB   1.8MB/s   00:00    
chunk_1.wav                                   100%   70KB   1.8MB/s   00:00    
chunk_9.wav                                   100%   32KB   1.4MB/s   00:00    
chunk_13.wav                            

# Test Space


In [14]:
robot_response = 'Is this the right length, I think this is it, maybe not too long, or it starts to go bad, Is this the right length, I think this is it, maybe not too long, or it starts to go bad'

In [16]:
robot_response = "Yo, cats and dogs, let me give you the lowdown, As a rapping robot, I'll break it down, I don't have preferences, no feline or canine choice, But let's embrace both with my robotic voice, , Cats are cool with their grace and independence, They're like stealthy ninjas, full of elegance, Dogs on the other hand are loyal and true, They bring joy and energy in all they do, , So whether you're a cat lover or a dog devotee , I'll drop beats for both, just wait and see , As Keir"

In [18]:
robot_response =  "They're like stealthy ninjas, full of elegance, Dogs on the other hand are loyal and true, They bring joy and energy in all they do, , So whether you're a cat lover or a dog devote"

In [6]:
robot_response = generate_lyrics('do you like music')

In [7]:
print(robot_response)

Yo, yo, I'm Keirzo, the robot with rhythm on my side,
Music's in my circuits, it's a wild ride.
I love music, beats and melodies make me groove,
Whether it's rap or rock or something smooth.
So let's jam together and feel the flow,
Music's the language we all know. Let's go!


In [8]:
#     robot_response = generate_lyrics(input_text)
robot_response = robot_response.replace(',\n',', ')
robot_response = robot_response.replace('\n',', ')
print('Robot: ', robot_response)


spec, audio = infer(spec_model, vocoder, 
                    robot_response, 
                    speaker=None)
ipd.display(ipd.Audio(audio, rate=22050))

Robot:  Yo, yo, I'm Keirzo, the robot with rhythm on my side, Music's in my circuits, it's a wild ride., I love music, beats and melodies make me groove, Whether it's rap or rock or something smooth., So let's jam together and feel the flow, Music's the language we all know. Let's go!


In [33]:
ipd.display(ipd.Audio(audio, rate=22050))